# CatBoost Optuna

## Load data

In [1]:
import pandas as pd

In [2]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')
train.head()

id cat0 cat1 cat2 cat3 cat4 cat5 cat6 cat7 cat8  ...     cont2     cont3  \
0   0    A    I    A    B    B   BI    A    S    Q  ...  0.759439  0.795549   
1   1    A    I    A    A    E   BI    K    W   AD  ...  0.386385  0.541366   
2   2    A    K    A    A    E   BI    A    E   BM  ...  0.343255  0.616352   
3   3    A    K    A    C    E   BI    A    Y   AD  ...  0.831147  0.807807   
4   4    A    I    G    B    E   BI    C    G    Q  ...  0.338818  0.277308   

      cont4     cont5     cont6     cont7     cont8     cont9    cont10 target  
0  0.681917  0.621672  0.592184  0.791921  0.815254  0.965006  0.665915      0  
1  0.388982  0.357778  0.600044  0.408701  0.399353  0.927406  0.493729      0  
2  0.793687  0.552877  0.352113  0.388835  0.412303  0.292696  0.549452      0  
3  0.800032  0.619147  0.221789  0.897617  0.633669  0.760318  0.934242      0  
4  0.610578  0.128291  0.578764  0.279167  0.351103  0.357084  0.328960      1  

[5 rows x 32 columns]

In [3]:
cat_cols = [x for x in train.columns if x.startswith('cat')]
cat_cols

['cat0',
 'cat1',
 'cat2',
 'cat3',
 'cat4',
 'cat5',
 'cat6',
 'cat7',
 'cat8',
 'cat9',
 'cat10',
 'cat11',
 'cat12',
 'cat13',
 'cat14',
 'cat15',
 'cat16',
 'cat17',
 'cat18']

In [4]:
from categorical_transform import CategoricalTransform,IntegerCategoricalTransform
ct = IntegerCategoricalTransform(cat_cols)
x_train = ct.fit_transform(train)
x_test = ct.transform(test)

In [5]:
x_train = train.drop(columns=['id','target'])
y_train = train['target']

In [6]:
from sklearn.model_selection import KFold
kfold = KFold(n_splits=5, shuffle=True)

# Try cont5 as golden feature

In [7]:
golden_index = x_train.columns.to_list().index('cont5')
golden_index

24

In [8]:
from categorical_transform import IntegerCategoricalTransform
from catboost import CatBoostClassifier
from sklearn.pipeline import Pipeline

In [9]:
cbc = CatBoostClassifier(cat_features=cat_cols, thread_count=6, verbose=False, 
                        per_float_feature_quantization='24:border_count=1024')
catboost_pipe = Pipeline([("trans", IntegerCategoricalTransform(cat_cols)),
                          ("catboost", cbc)])

In [10]:
from sklearn.model_selection import cross_validate
scores = cross_validate(catboost_pipe, X=x_train, y=y_train, cv=kfold, return_train_score = True,
                         scoring='roc_auc')

In [11]:
scores

{'fit_time': array([231.32033134, 232.74600649, 231.99849963, 233.42492723,
        233.30690217]),
 'score_time': array([2.12476325, 2.10229731, 2.12085533, 2.1158061 , 2.13367796]),
 'test_score': array([0.89508273, 0.89602997, 0.893517  , 0.89465777, 0.89189674]),
 'train_score': array([0.91121312, 0.91187613, 0.91188135, 0.91173585, 0.91204431])}

In [12]:
scores['test_score'].mean()

0.894236843014367

Not better

# Optuna optimization

In [13]:
from sklearn.metrics import roc_auc_score
import optuna
import numpy as np
from sklearn.model_selection import KFold
from catboost import CatBoostClassifier
from sklearn.pipeline import Pipeline

def objective(trial):
    params = {'iterations':10000,
              'depth': trial.suggest_int("depth", 4, 10),
              'l2_leaf_reg': trial.suggest_float("l2_leaf_reg", 0.0001, 25, log=True),
              'early_stopping_rounds':200,
              'eval_metric':'AUC',
              'use_best_model':True,
              'task_type':'CPU', 
              'cat_features':cat_cols,
              'verbose':True,
              'border_count':254,
              'thread_count':6
             }
    cbc = CatBoostClassifier(**params)
    kf = KFold(n_splits=5, shuffle=True)
    roc_test = []
    for train_index, test_index in kf.split(x_train):
        x_train_fold, x_test_fold = x_train.loc[train_index], x_train.loc[test_index]
        y_train_fold, y_test_fold = y_train.loc[train_index], y_train.loc[test_index]
        cbc.fit(x_train_fold, y_train_fold, eval_set=(x_test_fold, y_test_fold))    
        proba = cbc.predict_proba(x_test_fold)[:,1]
        roc_test.append(roc_auc_score(y_test_fold, proba))
    return np.mean(roc_test)

In [ ]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, timeout=5*60*60)
print(study.best_trial)

[I 2021-03-27 11:02:37,037] A new study created in memory with name: no-name-60ead0bc-5b00-4fe5-a073-ba3de6a65d18


0:	test: 0.8485421	best: 0.8485421 (0)	total: 303ms	remaining: 50m 25s
1:	test: 0.8576614	best: 0.8576614 (1)	total: 606ms	remaining: 50m 31s
2:	test: 0.8595916	best: 0.8595916 (2)	total: 879ms	remaining: 48m 48s
3:	test: 0.8595426	best: 0.8595916 (2)	total: 1.19s	remaining: 49m 28s
4:	test: 0.8645168	best: 0.8645168 (4)	total: 1.48s	remaining: 49m 18s
5:	test: 0.8662890	best: 0.8662890 (5)	total: 1.75s	remaining: 48m 43s
6:	test: 0.8674338	best: 0.8674338 (6)	total: 2.03s	remaining: 48m 18s
7:	test: 0.8676619	best: 0.8676619 (7)	total: 2.3s	remaining: 47m 52s
8:	test: 0.8678392	best: 0.8678392 (8)	total: 2.58s	remaining: 47m 50s
9:	test: 0.8676001	best: 0.8678392 (8)	total: 2.84s	remaining: 47m 14s
10:	test: 0.8677723	best: 0.8678392 (8)	total: 3.1s	remaining: 46m 55s
11:	test: 0.8680305	best: 0.8680305 (11)	total: 3.39s	remaining: 47m 3s
12:	test: 0.8680149	best: 0.8680305 (11)	total: 3.65s	remaining: 46m 41s
13:	test: 0.8679765	best: 0.8680305 (11)	total: 3.9s	remaining: 46m 19s
14:

113:	test: 0.8827625	best: 0.8827625 (113)	total: 31.7s	remaining: 45m 52s
114:	test: 0.8828112	best: 0.8828112 (114)	total: 32s	remaining: 45m 49s
115:	test: 0.8828670	best: 0.8828670 (115)	total: 32.3s	remaining: 45m 51s
116:	test: 0.8829176	best: 0.8829176 (116)	total: 32.6s	remaining: 45m 53s
117:	test: 0.8829756	best: 0.8829756 (117)	total: 32.9s	remaining: 45m 53s
118:	test: 0.8830341	best: 0.8830341 (118)	total: 33.2s	remaining: 45m 53s
119:	test: 0.8830791	best: 0.8830791 (119)	total: 33.5s	remaining: 45m 54s
120:	test: 0.8831279	best: 0.8831279 (120)	total: 33.7s	remaining: 45m 51s
121:	test: 0.8831956	best: 0.8831956 (121)	total: 34s	remaining: 45m 50s
122:	test: 0.8832298	best: 0.8832298 (122)	total: 34.3s	remaining: 45m 50s
123:	test: 0.8832856	best: 0.8832856 (123)	total: 34.6s	remaining: 45m 53s
124:	test: 0.8833244	best: 0.8833244 (124)	total: 34.9s	remaining: 45m 56s
125:	test: 0.8833572	best: 0.8833572 (125)	total: 35.2s	remaining: 45m 55s
126:	test: 0.8834105	best: 0.

224:	test: 0.8865691	best: 0.8865691 (224)	total: 1m 4s	remaining: 46m 23s
225:	test: 0.8865877	best: 0.8865877 (225)	total: 1m 4s	remaining: 46m 21s
226:	test: 0.8866106	best: 0.8866106 (226)	total: 1m 4s	remaining: 46m 22s
227:	test: 0.8866469	best: 0.8866469 (227)	total: 1m 4s	remaining: 46m 21s
228:	test: 0.8866691	best: 0.8866691 (228)	total: 1m 5s	remaining: 46m 20s
229:	test: 0.8867131	best: 0.8867131 (229)	total: 1m 5s	remaining: 46m 19s
230:	test: 0.8867305	best: 0.8867305 (230)	total: 1m 5s	remaining: 46m 18s
231:	test: 0.8867633	best: 0.8867633 (231)	total: 1m 5s	remaining: 46m 17s
232:	test: 0.8867886	best: 0.8867886 (232)	total: 1m 6s	remaining: 46m 17s
233:	test: 0.8868144	best: 0.8868144 (233)	total: 1m 6s	remaining: 46m 16s
234:	test: 0.8868551	best: 0.8868551 (234)	total: 1m 6s	remaining: 46m 15s
235:	test: 0.8868785	best: 0.8868785 (235)	total: 1m 7s	remaining: 46m 16s
236:	test: 0.8869051	best: 0.8869051 (236)	total: 1m 7s	remaining: 46m 17s
237:	test: 0.8869461	best

333:	test: 0.8885621	best: 0.8885621 (333)	total: 1m 36s	remaining: 46m 19s
334:	test: 0.8885640	best: 0.8885640 (334)	total: 1m 36s	remaining: 46m 18s
335:	test: 0.8885819	best: 0.8885819 (335)	total: 1m 36s	remaining: 46m 18s
336:	test: 0.8885981	best: 0.8885981 (336)	total: 1m 36s	remaining: 46m 18s
337:	test: 0.8886139	best: 0.8886139 (337)	total: 1m 37s	remaining: 46m 17s
338:	test: 0.8886211	best: 0.8886211 (338)	total: 1m 37s	remaining: 46m 17s
339:	test: 0.8886315	best: 0.8886315 (339)	total: 1m 37s	remaining: 46m 18s
340:	test: 0.8886422	best: 0.8886422 (340)	total: 1m 38s	remaining: 46m 18s
341:	test: 0.8886548	best: 0.8886548 (341)	total: 1m 38s	remaining: 46m 17s
342:	test: 0.8886643	best: 0.8886643 (342)	total: 1m 38s	remaining: 46m 17s
343:	test: 0.8886889	best: 0.8886889 (343)	total: 1m 38s	remaining: 46m 17s
344:	test: 0.8887044	best: 0.8887044 (344)	total: 1m 39s	remaining: 46m 16s
345:	test: 0.8887112	best: 0.8887112 (345)	total: 1m 39s	remaining: 46m 15s
346:	test: 0

...

4603:	test: 0.8926052	best: 0.8926076 (4600)	total: 12m	remaining: 14m 4s
4604:	test: 0.8926041	best: 0.8926076 (4600)	total: 12m 1s	remaining: 14m 4s
4605:	test: 0.8926057	best: 0.8926076 (4600)	total: 12m 1s	remaining: 14m 4s
4606:	test: 0.8926059	best: 0.8926076 (4600)	total: 12m 1s	remaining: 14m 4s
4607:	test: 0.8926101	best: 0.8926101 (4607)	total: 12m 1s	remaining: 14m 4s
4608:	test: 0.8926108	best: 0.8926108 (4608)	total: 12m 1s	remaining: 14m 4s
4609:	test: 0.8926108	best: 0.8926108 (4608)	total: 12m 1s	remaining: 14m 3s
4610:	test: 0.8926118	best: 0.8926118 (4610)	total: 12m 2s	remaining: 14m 3s
4611:	test: 0.8926110	best: 0.8926118 (4610)	total: 12m 2s	remaining: 14m 3s
4612:	test: 0.8926110	best: 0.8926118 (4610)	total: 12m 2s	remaining: 14m 3s
4613:	test: 0.8926101	best: 0.8926118 (4610)	total: 12m 2s	remaining: 14m 3s
4614:	test: 0.8926099	best: 0.8926118 (4610)	total: 12m 2s	remaining: 14m 3s
4615:	test: 0.8926119	best: 0.8926119 (4615)	total: 12m 2s	remaining: 14m 3s
46

4709:	test: 0.8926324	best: 0.8926354 (4702)	total: 12m 17s	remaining: 13m 48s
4710:	test: 0.8926317	best: 0.8926354 (4702)	total: 12m 17s	remaining: 13m 48s
4711:	test: 0.8926312	best: 0.8926354 (4702)	total: 12m 17s	remaining: 13m 48s
4712:	test: 0.8926312	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4713:	test: 0.8926315	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4714:	test: 0.8926317	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4715:	test: 0.8926318	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4716:	test: 0.8926305	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4717:	test: 0.8926303	best: 0.8926354 (4702)	total: 12m 18s	remaining: 13m 47s
4718:	test: 0.8926317	best: 0.8926354 (4702)	total: 12m 19s	remaining: 13m 47s
4719:	test: 0.8926307	best: 0.8926354 (4702)	total: 12m 19s	remaining: 13m 46s
4720:	test: 0.8926314	best: 0.8926354 (4702)	total: 12m 19s	remaining: 13m 46s
4721:	test: 0.8926313	best: 0.8926354 (4702)	total: 

4813:	test: 0.8926661	best: 0.8926670 (4812)	total: 12m 34s	remaining: 13m 32s
4814:	test: 0.8926654	best: 0.8926670 (4812)	total: 12m 34s	remaining: 13m 32s
4815:	test: 0.8926648	best: 0.8926670 (4812)	total: 12m 34s	remaining: 13m 32s
4816:	test: 0.8926636	best: 0.8926670 (4812)	total: 12m 34s	remaining: 13m 32s
4817:	test: 0.8926641	best: 0.8926670 (4812)	total: 12m 34s	remaining: 13m 31s
4818:	test: 0.8926649	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4819:	test: 0.8926639	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4820:	test: 0.8926637	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4821:	test: 0.8926642	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4822:	test: 0.8926623	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4823:	test: 0.8926621	best: 0.8926670 (4812)	total: 12m 35s	remaining: 13m 31s
4824:	test: 0.8926620	best: 0.8926670 (4812)	total: 12m 36s	remaining: 13m 30s
4825:	test: 0.8926629	best: 0.8926670 (4812)	total: 

4917:	test: 0.8926890	best: 0.8926890 (4917)	total: 12m 50s	remaining: 13m 16s
4918:	test: 0.8926898	best: 0.8926898 (4918)	total: 12m 51s	remaining: 13m 16s
4919:	test: 0.8926894	best: 0.8926898 (4918)	total: 12m 51s	remaining: 13m 16s
4920:	test: 0.8926895	best: 0.8926898 (4918)	total: 12m 51s	remaining: 13m 16s
4921:	test: 0.8926902	best: 0.8926902 (4921)	total: 12m 51s	remaining: 13m 15s
4922:	test: 0.8926910	best: 0.8926910 (4922)	total: 12m 51s	remaining: 13m 15s
4923:	test: 0.8926908	best: 0.8926910 (4922)	total: 12m 51s	remaining: 13m 15s
4924:	test: 0.8926903	best: 0.8926910 (4922)	total: 12m 51s	remaining: 13m 15s
4925:	test: 0.8926904	best: 0.8926910 (4922)	total: 12m 52s	remaining: 13m 15s
4926:	test: 0.8926904	best: 0.8926910 (4922)	total: 12m 52s	remaining: 13m 15s
4927:	test: 0.8926902	best: 0.8926910 (4922)	total: 12m 52s	remaining: 13m 15s
4928:	test: 0.8926914	best: 0.8926914 (4928)	total: 12m 52s	remaining: 13m 14s
4929:	test: 0.8926912	best: 0.8926914 (4928)	total: 

5023:	test: 0.8927317	best: 0.8927317 (5023)	total: 13m 7s	remaining: 13m
5024:	test: 0.8927326	best: 0.8927326 (5024)	total: 13m 7s	remaining: 13m
5025:	test: 0.8927329	best: 0.8927329 (5025)	total: 13m 8s	remaining: 12m 59s
5026:	test: 0.8927332	best: 0.8927332 (5026)	total: 13m 8s	remaining: 12m 59s
5027:	test: 0.8927324	best: 0.8927332 (5026)	total: 13m 8s	remaining: 12m 59s
5028:	test: 0.8927324	best: 0.8927332 (5026)	total: 13m 8s	remaining: 12m 59s
5029:	test: 0.8927327	best: 0.8927332 (5026)	total: 13m 8s	remaining: 12m 59s
5030:	test: 0.8927323	best: 0.8927332 (5026)	total: 13m 8s	remaining: 12m 59s
5031:	test: 0.8927336	best: 0.8927336 (5031)	total: 13m 9s	remaining: 12m 59s
5032:	test: 0.8927364	best: 0.8927364 (5032)	total: 13m 9s	remaining: 12m 58s
5033:	test: 0.8927380	best: 0.8927380 (5033)	total: 13m 9s	remaining: 12m 58s
5034:	test: 0.8927400	best: 0.8927400 (5034)	total: 13m 9s	remaining: 12m 58s
5035:	test: 0.8927399	best: 0.8927400 (5034)	total: 13m 9s	remaining: 12

In [ ]:
study.best_params

In [ ]:
study.best_value

In [ ]:
len(study.trials)

In [ ]:
from optuna.visualization import plot_optimization_history, plot_param_importances
plot_optimization_history(study)

In [ ]:
plot_param_importances(study)